# Hybrid rule-based statistical language model

## add gazetteers to all the categories

This notebook loads the scispacy model and adds look-up lists to the model for cells/proteins, to increase accuracy. The lists come from WikiData.

- cell lines 
- enzymes 
- wiki garbage 
    - wiki lab
    - download csvs for proteins?

In [2]:
import spacy 

nlp = spacy.load('models/scipy_imba')

In [4]:
from spacy.pipeline import EntityRuler

ruler = EntityRuler(nlp)


## Cellosaurus

In [6]:

cell_patterns = []



with open('listar/cells/wikidata.csv') as cello:
    for l in cello.readlines():
        cell_patterns.append(
         {"label": "cell_line", "pattern": l.strip()}
        )
        
        
with open('listar/cells/synonyms.txt') as cello:
    for l in cello.readlines():
        cell_patterns.append(
         {"label": "cell_line", "pattern": l.strip()}
        )

In [7]:
cell_patterns

[{'label': 'cell_line', 'pattern': 'itemLabel'},
 {'label': 'cell_line', 'pattern': 'CHO'},
 {'label': 'cell_line', 'pattern': 'HEK293'},
 {'label': 'cell_line', 'pattern': 'Jurkat'},
 {'label': 'cell_line', 'pattern': 'MCF-7'},
 {'label': 'cell_line', 'pattern': 'Peer'},
 {'label': 'cell_line', 'pattern': 'Sf21'},
 {'label': 'cell_line', 'pattern': 'Vero'},
 {'label': 'cell_line', 'pattern': 'MRC-5'},
 {'label': 'cell_line', 'pattern': 'Raji'},
 {'label': 'cell_line', 'pattern': '3T3-L1'},
 {'label': 'cell_line', 'pattern': 'NIH 3T3'},
 {'label': 'cell_line', 'pattern': 'A-431'},
 {'label': 'cell_line', 'pattern': 'A-549'},
 {'label': 'cell_line', 'pattern': 'AB.9'},
 {'label': 'cell_line', 'pattern': 'BCP-1'},
 {'label': 'cell_line', 'pattern': 'BOSC-23'},
 {'label': 'cell_line', 'pattern': 'BHK-21'},
 {'label': 'cell_line', 'pattern': 'C2C12'},
 {'label': 'cell_line', 'pattern': 'COS cell lines'},
 {'label': 'cell_line', 'pattern': 'Caco-2'},
 {'label': 'cell_line', 'pattern': 'DU14

In [7]:
ruler.add_patterns(cell_patterns)
nlp.add_pipe(ruler)

In [92]:
doc = nlp('HEK293 is my favourite cell line. Although, HSC-2 is not far behind')

In [93]:
print([(ent.text, ent.label_) for ent in doc.ents])

[('HEK293', 'cell_line'), ('cell', 'protein'), ('HSC-2', 'cell_line'), ('not', 'protein'), ('far', 'protein')]


# Worked!    SAVE so don't need to add the patterns again

In [16]:
ruler.to_disk("models/ruler")    # saves patterns and config

# Wiki Labelled

In [10]:
import json 

with open('wiki_labelled.json') as dico:
    js = json.load(dico)

In [11]:
js

[['ABT', 'compound'],
 ['ACP', 'protein'],
 ['ACP', 'gene'],
 ['ADR', 'gene'],
 ['ALS', 'protein'],
 ['ALS', 'gene'],
 ['ALS', 'compound'],
 ['AML3', 'gene'],
 ['APC', 'protein'],
 ['APC', 'gene'],
 ['APC', 'compound'],
 ['APO', 'gene'],
 ['APS', 'gene'],
 ['APS', 'compound'],
 ['ATG', 'compound'],
 ['ATT', 'compound'],
 ['ATTR', 'protein'],
 ['ATTR', 'gene'],
 ['Ang', 'protein'],
 ['Ang', 'gene'],
 ['Axin1', 'protein'],
 ['Axin1', 'gene'],
 ['Axl', 'protein'],
 ['Axl', 'gene'],
 ['BAPN', 'compound'],
 ['BF', 'compound'],
 ['BMP', 'protein'],
 ['BMP', 'gene'],
 ['BMP', 'compound'],
 ['BPS', 'compound'],
 ['BTP2', 'gene'],
 ['BTP2', 'compound'],
 ['Blimp1', 'gene'],
 ['CAT2', 'protein'],
 ['CAT2', 'gene'],
 ['CD102', 'gene'],
 ['CD14', 'protein'],
 ['CD14', 'gene'],
 ['CD4', 'protein'],
 ['CD4', 'gene'],
 ['CD4', 'compound'],
 ['CD63', 'protein'],
 ['CD63', 'gene'],
 ['CDK1', 'protein'],
 ['CDK1', 'gene'],
 ['CDK2', 'protein'],
 ['CDK2', 'gene'],
 ['CFI1', 'gene'],
 ['CKD', 'gene'],
 ['

# Wiki Labelled, fetch lists

In [1]:

    
def is_wikidata(candidate, wikiQx, prop):
    """
    wikiQx: category ('object' in wikidata triple )
    prop: property, like P31 or P279
    """
    url = 'https://query.wikidata.org/sparql'

    query = """
    SELECT 
      ?item ?itemLabel
    WHERE {{
      ?item wdt:{} wd:{}.
      ?item ?label "{}"@en .
  SERVICE wikibase:label {{ bd:serviceParam wikibase:language "en". }}
    }}
    """.format(prop,wikiQx,candidate)


    #Pick a random user agent
    user_agent = random.choice(user_agent_list)
    #Set the headers 
    headers = {'User-Agent': user_agent}
    #Make the request
  

    r = requests.get(url, params = {'format': 'json', 'query': query},headers=headers)
    try:
        data = r.json()
    except:
        print(r.text)

    if data['results']['bindings'] != []:
        return True
    else:
        return False
    
    
    
def is_wikidata_alt(candidate, wikiQx, prop):
    """
    wikiQx: category ('object' in wikidata triple )
    """
    url = 'https://query.wikidata.org/sparql'

    query = """
    SELECT 
      ?item ?itemLabel
    WHERE {{
      ?item wdt:{} wd:{}.
      ?item skos:altLabel "{}"@en .
  SERVICE wikibase:label {{ bd:serviceParam wikibase:language "en". }}
    }}
    """.format(prop,wikiQx,candidate)

    #Pick a random user agent
    user_agent = random.choice(user_agent_list)
    #Set the headers 
    headers = {'User-Agent': user_agent}
    #Make the request
    
    r = requests.get(url, params = {'format': 'json', 'query': query}, headers=headers)
    try:
        data = r.json()
    except:
        print(r.text)

    if data['results']['bindings'] != []:
        return True
    else:
        return False

# Proteins

fetched through the query interface on wikidata

In [17]:
import pandas as pd 

protein_dir = '/Users/valdimareggertsson/Documents/Valdi/Vetrarönn 2019/NER/Listar/proteins/'


protein_df = pd.read_csv(protein_dir + 'proteins_wiki.csv')


In [22]:
protein_alts = pd.read_csv(protein_dir + 'proteins_wiki_alts.csv')


In [27]:
protein_names =  list(protein_df['itemLabel'])
protein_names.extend( list( protein_alts['altLabel']   )  )

In [29]:
protein_patterns = []

for p in protein_names:
    protein_patterns.append( {'label': 'protein', 'pattern': p}  )

# Add the protein patterns in batches to the ruler

In [34]:
batch_size = 10000
ruler.add_patterns(protein_patterns[0 : batch_size])
ruler.add_patterns(protein_patterns[batch_size : 2*batch_size])



In [35]:
ruler.add_patterns(protein_patterns[2*batch_size : 5*batch_size])

In [36]:
ruler.add_patterns(protein_patterns[5*batch_size : 10*batch_size])

In [37]:
ruler.add_patterns(protein_patterns[10*batch_size : 20*batch_size])

In [38]:
ruler.add_patterns(protein_patterns[20*batch_size : 40*batch_size])

In [39]:
ruler.add_patterns(protein_patterns[40*batch_size : 80*batch_size])

In [57]:
ruler.add_patterns(protein_patterns[80*batch_size : 120*batch_size])

In [58]:
ruler.add_patterns(protein_patterns[120*batch_size : 150*batch_size])

In [60]:
ruler.add_patterns(protein_patterns[150*batch_size : 180*batch_size])

In [63]:
ruler.add_patterns(protein_patterns[180*batch_size : 200*batch_size])

In [66]:
ruler.add_patterns(protein_patterns[200*batch_size : 220*batch_size])

In [69]:
ruler.add_patterns(protein_patterns[220*batch_size : ])

In [70]:
ruler.to_disk("models/ruler")    # saves patterns and config

In [67]:
from math import isnan

for i,p in enumerate(protein_patterns[200*batch_size : ]):

    # Remove nan: 
    if not isinstance(p['pattern'], str):
        protein_patterns.remove(p)
        
    if len(p['pattern']) > 20:
        print(p['pattern'])

NADPH:adrenodoxin oxidoreductase, mitochondrial
PI-PLC X domain-containing protein 1-like
uncharacterized protein LOC100003714
MAM domain-containing protein 2
low-density lipoprotein receptor-related protein 12
arylamine N-acetyltransferase-like
arylamine N-acetyltransferase, pineal gland isozyme NAT-3
7 transmembrane receptor
histamine H1 receptor
ras homolog gene family, member H
rho-related GTP-binding protein RhoH
ras-like protein Rhoh
serine/threonine-protein kinase LMTK2
serine/threonine-protein kinase LMTK2-like
uncharacterized protein LOC566185
zinc finger FYVE domain-containing protein 16
solute carrier family 13 member 4
solute carrier family 13 (sodium/sulfate symporter), member 4
coiled-coil domain-containing protein 15
opioid receptor, delta 1b
RAC-beta serine/threonine-protein kinase
beta-3-galactosyltransferase (ssp2)
four and a half LIM domains 5
gastrula zinc finger protein XlCGF57.1-like
gastrula zinc finger protein XlCGF8.2DB-like
somatostatin receptor type 5
inward 

PH domain containing protein
variant surface glycoprotein (VSG
palmitoyl acyltransferase 5
variant surface glycoprotein (VSG)
variant surface glycoprotein (VSG
replication factor c subunit 1
variant surface glycoprotein (VSG)
variant surface glycoprotein (VSG)
expression site-associated gene 1 (ESAG1) protein
Methyltransferase TYW3
expression site-associated gene 11 (ESAG11) protein
expression site-associated gene 2 (ESAG2) protein
leucine-rich repeat protein (LRRP)
39s ribosomal protein l4 mitochondrial
adenosine transporter
cleavage and polyadenylation specificity factor 30 kDa subunit
acyl-CoA binding protein
N-acetyltransferase complex ARD1 subunit
ATP-dependent DEAD/H RNA helicase
RNA binding protein EIF1AD
Domain of unknown function (DUF4464)
kinetoplast-associated protein-like protein
CMGC/RCK protein kinase
DEAD/DEAH box helicase-like protein
Uncharacterised protein family (UPF0160)
RING-variant domain containing protein
amino acid permease 24
CorA-like Mg2+ transporter protein

2OG-Fe(II) oxygenase superfamily
Sas10/Utp3/C1D family/Sas10 C-terminal domain containing protein
Staphylococcal nuclease homologue
26S proteasome non ATPase regulatory subunit
kinetoplast poly(A) polymerase 1
kinetoplastid-specific dual specificity phosphatase
calmodulin-like protein
RNA polymerase B subunit RPB8
RNA binding protein rbp16
C-1-tetrahydrofolate synthase
6-phosphofructo-2-kinase/fructose-2
Cleavage factor I 25 kDa subunit
DNA replication licensing factor MCM2
ras-like small GTPase
ribonucleoside-diphosphate reductase large chain
endonuclease/exonuclease/phosphatase-like protein
ribosomal RNA processing protein 4
ribosomal RNA adenine dimethylase family protein
mitochondrial carrier protein
mitochondrial RNA binding protein 1
AUT2/APG4/ATG4 cysteine peptidase
Mitochondrial ribosomal protein L46
Sad1 / UNC-like C-terminal
Rab-GTPase-TBC domain containing protein
pumilio/PUF RNA binding protein 5
endosomal integral membrane protein
mitogen-activated protein kinase 12
Alpha/

tubulin polymerization promoting protein family
E3 ubiquitin protein ligase TRIM9
ubiquitin-conjugating enzyme variant Kua homologue
vacuolar protein sorting-associated protein 35
tripartite motif protein trim
chaperone protein DnaJ
SNARE domain containing protein
pyruvate dehydrogenase complex E3 binding protein
Lupus La protein homolog
Tetratricopeptide repeat
receptor-type adenylate cyclase GRESAG 4
protein translation factor sui1
DnaJ domain containing protein
predicted zinc finger protein
cAMP-dependent protein kinase catalytic subunit 1
U5 snRNA-associated splicing factor
PRP8 protein homologue
tegument-associated antigen
Chromosome passenger complex (CPC) protein INCENP N terminal
unc-50 related protein homolog
tRNA import complex component
Mitochondrial import inner membrane translocase subunit TIM42
E3 ubiquitin protein ligase HECTD1
tegument-allergen-like protein
calmodulin-like protein
EF hand containing protein
predicted WD40 repeat protein
nucleoside diphosphate kinase
teg

Cytosolic carboxypeptidase-like protein 5
Zinc finger RING type
FHA domain containing protein
Domain of unknown function (DUF4586)
catalytic subunit of the vacuolar transporter chaperone 4
ATP-dependent protease ATPase subunit HslU2
Variant Surface Glycoprotein
variant surface glycoprotein (VSG)
Variant Surface Glycoprotein
Variant Surface Glycoprotein
Variant Surface Glycoprotein
Variant Surface Glycoprotein
5 hydroxytryptamine receptor 1B
variant surface glycoprotein (VSG
variant surface glycoprotein (VSG
variant surface glycoprotein (VSG
variant surface glycoprotein (VSG)
variant surface glycoprotein (VSG)
structural maintenance of chromosomes protein 3
variant surface glycoprotein (VSG
BAC from homologous region on chr8
variant surface glycoprotein (VSG
BAC from homologous region on chr8
variant surface glycoprotein (VSG)
BAC from homologous region on chr8
variant surface glycoprotein (VSG
BAC from homologous region on chr8
variant surface glycoprotein (VSG
BAC from homologous regi

...

conserved hypothetical protein
phosphatidylinositol 4-kinase
serine/threonine-protein kinase chk2
conserved hypothetical protein
serine/threonine-protein kinase crk1
conserved hypothetical protein
G-patch RNA maturation protein
conserved hypothetical protein
conserved hypothetical protein
glyoxalase/bleomycin resistance protein/dioxygenase
EF hand domain-containing protein
conserved hypothetical protein
conserved hypothetical protein
conserved hypothetical protein
conserved hypothetical protein
RNA polymerase II transcription factor B subunit 5
conserved hypothetical protein
1,3-beta-glucanosyltransferase gel1 precursor
conserved hypothetical protein
conserved hypothetical protein
imidazole glycerol phosphate synthase hisHF
PQ loop repeat protein
conserved hypothetical protein
conserved hypothetical protein
guanine nucleotide-binding protein alpha-2 subunit
conserved hypothetical protein
conserved hypothetical protein
glutamate-cysteine ligase
GNAT family N-acetyltransferase
conserved 

coagulation factor 5/8 type domain-containing protein
nucleotide-sugar transporter
50S ribosomal protein L14
RNP domain-containing protein
histone-lysine N-methyltransferase SET9
6-phosphogluconate dehydrogenase
serine/threonine protein phosphatase 2A
40S ribosomal protein S11
palmitoyltransferase pfa3
glutamate carboxypeptidase-1
hypothetical phospholipase C
NADH-cytochrome b5 reductase-2
hypothetical aspartyl protease
tripeptidyl-peptidase 1
kinetochore protein-17
Ornithine decarboxylase
hypothetical aspartyl protease
DNA repair protein RAD16
hypothetical aspartyl protease
aromatic ring-opening dioxygenase LigB subunit
acyl-protein thioesterase 1
MOSC domain-containing protein
multi-drug resistance-5
metalloreductase transmembrane component
FAD-dependent oxidoreductase-2
Eukaryotic translation initiation factor 3 subunit G
Short chain dehydrogenase
Sec1 family superfamily protein
CBF/NF-Y family transcription factor
Phosphatidylethanolamine N-methyltransferase
palmitoyltransferase er

metacaspase-1 precursor
2-dehydropantoate 2-reductase
alpha/beta hydrolase fold protein
glycosyl hydrolase family 31-4
ZZ type zinc finger domain-containing protein
multi-drug resistance-11
aspartic endopeptidase
mitochondrial import receptor subunit tom-70
U3 small nucleolar ribonucleoprotein IMP4
3-hydroxy-3-methylglutaryl-coenzyme A reductase
regulator-nonsense transcripts 1
FAD binding domain-containing protein
cation-transporting ATPase 4
SUMO-conjugating enzyme ubc9
asparagine synthetase
nucleotide-binding protein 2
NADH-cytochrome b5 reductase-3
multidrug transporter
ATP-dependent RNA helicase dbp-7
general stress protein 39
niemann-Pick C1 protein
ribosomal L1 domain-containing protein 1
transcription factor-15
palmitoyl-protein thioesterase
dihydroorotate reductase PyrE
palmitoyltransferase SWF1
DUF895 domain membrane protein
transporter SEC61 subunit alpha
kynurenine 3-monooxygenase
CAMK/CAMKL/AMPK protein kinase
oxysterol binding protein
transcription elongation factor spt6


Lanthionine synthetase C family protein
herpesviridae ul52/ul70 dna primase
Superkiller viralicidic activity 2 family 2
radical SAM domain-containing protein
protein phosphatase 2b regulatory subunit
iron-sulfur cluster protein ISCA
Ufm1-conjugating enzyme 1
MORN repeat-containing protein
UBA/TS-N domain-containing protein
Myb family DNA-binding domain-containing protein
regulator of chromosome condensation rcc1
3' exoribonuclease family
CHCH domain-containing protein
ribosomal RNA small subunit methyltransferase B
mitochondrial inner membrane translocase subunit TIM17
ENTH domain-containing protein
SAG-related sequence SRS46
rRNA pseudouridine synthase
bromodomain-containing protein
alpha-glucan water dikinase 1
translation initiation factor IF-2
phosphoadenosine phosphosulfate reductase family protein
eIF2 kinase IF2K-A (incomplete catalytic triad)
ribosomal protein RPS23
autophagy-related protein 7 atg7
OTU family cysteine protease
EF hand domain-containing protein
p25-alpha family 

Sterol uptake control 2
translation initiation factor IF-2
MFS multidrug transporter
translation initiation factor eIF-2B subunit epsilon
Phospholipid:diacylglycerol acyltransferase
uroporphyrinogen-III synthase
DASH complex subunit dad4
glucose-repressible alcohol dehydrogenase transcriptional effector
bZIP family transcription factor
Oligopeptide transporter
26S proteasome regulatory subunit N6
MFS SP general alpha glucoside:H+ symporter
asparaginyl-tRNA synthetase
ubiquitin-conjugating enzyme
ribosome biogenesis ATPase RIX7
cell division control 25
Sterol uptake control 2
guanine nucleotide exchange factor LTE1
vacuolar ATP synthase subunit d
D-xylose-proton symporter
endoribonuclease L-PSP
6-hydroxy-D-nicotine oxidase
Choline dehydrogenase
glutathione s-transferase
positive regulator of purine utilization
general alpha-glucoside permease
MFS SP general alpha glucoside:H+ symporter
Aromatic peroxygenase
Sterol uptake control 2
endo-1,4-beta-xylanase B
SPEG neighbor protein
uncharact

In [68]:
len(protein_patterns) / batch_size

242.4103

In [91]:
doc = nlp('Jurkat 1.56*10^6 cells per ml 75.5% viability.')

In [90]:
print([(ent.text, ent.label_) for ent in doc.ents])

[('Jurkats', 'cell_line'), ('6', 'cell_line'), ('per', 'protein'), ('viability', 'protein')]


# Enzyme regexp

In [81]:
enzyme_pattern = {
    'label': 'enzyme', 
    'pattern': [{"TEXT": {"REGEX": r'ase\b'}}]
}

In [1]:
nlp2 = spacy.load('models/scipy_imba')

NameError: name 'spacy' is not defined

In [83]:
ruler = EntityRuler(nlp2)

ruler.add_patterns([enzyme_pattern])

In [84]:
doc = nlp2('my favorite enzyme is protease along with hydrogenase')

In [85]:
print([(ent.text, ent.label_) for ent in doc.ents])

[]


In [38]:
import re
pattern = re.compile("ase$")
if pattern.match('protease'):
    print('ye')
else:
    print('ne')

ne


In [72]:
re.search(r'\bfull\b', 'I am full now ')

<re.Match object; span=(0, 4), match='full'>

In [86]:
re.findall(r'ase\b', 'my favorite enzyme is protease along with hydrogenase')

['ase', 'ase']

### Test

In [ ]:
with open('/Users/valdimareggertsson/Documents/Valdi/Vetrarönn 2019/NER') as f.



In [ ]:
    bbb

# Throw away fake proteins

In [ ]:
ruler = EntityRuler(nlp)
ruler.from_disk("models/ruler")    # saves patterns and config